<div style="padding:30px; color: white; background-color: #0071CD">
<center>
<img src="img/logoub.jpeg"></img>
<center>
<p>
<h1>Algorítmica Avanzada</h1>
<h2>Práctica 1 - Grafos </h2>
</center>
</p>
</div>

<div class="alert alert-danger" style="width:95%; margin:0 auto; padding">
<center><p><h2> ¡¡IMPORTANTE!! </h2></p> </center> 

<p>
Para la realización de esta práctica tendréis que utilizar la clase de grafos NetworkX y <b>NO</b> la clase `Graph` que implementasteis en la Práctica 0. Hay casos muy concretos que no contemplaban los tests y podría hacer que vuestros algoritmos no funcionen correctamente. NetworkX tiene una interfaz muy similar a la librería <i>Graph</i> que implementasteis la semana pasada. Para más información podéis consultar la documentación de la librería <a href="https://networkx.github.io/documentation/latest/reference/introduction.html">aquí.</a>
</p>
</div>

<div class="alert alert-info">
<center>
  <h1>Introducción</h1>
</center>

A lo largo de esta práctica trabajaremos con el grafo generado a partir de la red de metro de Londres. En este grafo, los nodos representan las estaciones y las aristas las vias que van de una estación a otra. Todas las aristas tienen cuatro atributos:

* Linea
* Color
* Nombre (de la linea)
* Distancia

Los nodos contienen: 
* El nombre de la estación
* La latitud y longitud de la estación
* Número de lineas
* Zona


In [1]:
from util import get_subway_graph, draw_subway_graph
from networkx import nx

# Carga del grafo del metro con el que trabajaremos
G, lines = get_subway_graph('csv')

# Algunos nodos
print(list(G.nodes())[:20],'...')
# Algunas aristas
print(list(G.edges())[:20],'...')
print(len(G))
print('\n')
print("Ejemplo de arista: ",G.edges[156,167])
print("Ejemplo de nodo: ",G.node[33])

[11, 163, 212, 49, 87, 197, 82, 193, 84, 148, 279, 113, 246, 298, 114, 140, 137, 206, 237, 143] ...
[(11, 163), (11, 212), (11, 83), (11, 104), (11, 28), (11, 249), (11, 94), (163, 82), (212, 192), (49, 87), (49, 197), (49, 151), (87, 279), (87, 255), (87, 285), (197, 192), (197, 107), (197, 151), (82, 193), (193, 278)] ...
306


Ejemplo de arista:  {'name': 'Metropolitan Line', 'color': '8b004c', 'stripe': 'NULL', 'line': 8, 'distance': 0.006350590523722737}
Ejemplo de nodo:  {'latitude': 51.5269, 'longitude': -0.0247, 'name': 'Bow Road', 'display_name': 'Bow<br />Road', 'zone': 2.0, 'total_lines': 2, 'rail': '0'}


Para más consultas, la información ha sido extraida de Wikimedia Commons:

https://commons.wikimedia.org/wiki/London_Underground_geographic_maps/CSV

# util.py

En este archivo se os facilitan varias funciones que os permitiran cargar y visualizar la red de metro.
```python
"""
Retorna un objeto nx.Graph que corresponde al grafo de la red de metro y un 
diccionario con las lineas del metro
 - location: ruta donde esta almacenado el archivo .csv
"""
G, lines = get_subway_graph(location)

"""
Dibuja el grafo que le pasemos por parametro.
- G: Grafo de la red de metro
- lines: diccionario con la información sobre las lineas del metro
- figsize: parametro opcional que nos permite definir el tamaño de la figura
- show_labels: parametro opcional que nos permite indicar si queremos mostrar los 
    nombres de las estaciones
"""
draw_subway_graph(G, lines, figsize=(10,6), show_labels=False)

```

In [2]:
draw_subway_graph(G, lines, figsize=(400,360))

C:\Users\dragr\Anaconda3\lib\site-packages\networkx\drawing\nx_pylab.py:579: MatplotlibDeprecationWarning: 
The iterable function was deprecated in Matplotlib 3.1 and will be removed in 3.3. Use np.iterable instead.
  if not cb.iterable(width):


<div class="alert alert-info">
<center>
  <h1>Contenido</h1>
  </center><p>



<div class="alert alert-success" style="width:90%; margin:0 auto;">

  <h2><p>1- Dijkstra</p></h2>
  <p>
 En esta segunda parte de la práctica se propone que implementéis el algoritmo <a href="https://en.wikipedia.org/wiki/Dijkstra%27s_algorithm">Dijkstra</a> (explicado en teoría) para encontrar el camino más corto entre dos paradas de la red de metro de Londres.
</p>



<div class="alert alert-danger" style="width:80%; margin:0 auto; padding">
<center><p><h3> Código </h3></p> </center>
<p>
<h3>INPUT</h3>
<ul>
<li>__G__: Este es el grafo (en el caso de esta practica la red de metro) que utilizaremos para buscar el camino. Debe de ser un objeto de tipo 'nx.Graph'.</li>
<li>__origen__: Este parámetro corresponde al índice de un nodo. En este caso, como indexamos los nodos con el identificador de las paradas de Metro, deberá ser un entero _(e.g. 231)_.</li>
<li>__destino__: El indice del nodo al que queremos llegar. Igual que el origen, deberá ser un entero.</li>
<li>__infinity=*(int)*__: Parametro opcional en el que definimos que numero nos va bien para utilizar como infinito en el momento de inicializar los pesos de los nodos.</li>
</ul>
<br>
<h3>OUTPUT</h3>
El output de una funcion es un <b>diccionario</b> que contiene los siguientes valores
<ul>
<li>__ _'path'_ __: Una lista de índices correspondientes al camino encontrado del nodo inicial al nodo final (ambos nodos, inicio y final, han de estar incluidos en esta lista).</li>
<li>__ _'expanded'_ __: El numero de nodos que se han visitado para encontrar la solución.</li>
<li>__ _'distance'_ __: La distancia del camino mínimo desde el origen hasta el destino (es decir, el valor del nodo destino).
<ul>

</p>
</div>


In [3]:
import heapq

def backtracking(origen, key, prevs): #Función de backtracking para devolver al final.
    ret_list = []
    while key != origen:
        ret_list.append(key)
        key = prevs.get(key)
        
    ret_list.append(origen)
    ret_list.reverse()
    return ret_list


def dijkstra(G, origen, destino, infinity=2**32-1):
    #Declaración de las estructuras de datos de apoyo que usaré.
    heap, visited = [], set()
    prevs, aux_dist = {}, {}
    expanded = 0
    
    #Inicialización de distancias y heap, separamos origen.
    for vertex in G.nodes(): #O(n)
        aux_dist[vertex] = infinity
        
    heapq.heappush(heap,[0, origen])
    aux_dist[origen] = 0
            
    while heap:#O((v+e)logv), peor caso O(e log v).
        #Obtenemos cada nodo desde donde buscaremos vecinos y lo marcamos como visitado.
        distance, node = heapq.heappop(heap)
        visited.add(node)
        expanded += 1        
        
        if node == destino:#Encontramos el nodo buscado, enviamos
            BFRL = backtracking(origen, destino, prevs)
            return{'path' : BFRL, 'expanded' : expanded, 'distance' : distance}
        
        for neighbor in list(G.neighbors(node)): #Buscamos entre los vecinos del nodo
            if neighbor not in visited: #Cogemos solo aquellos que no estén visitados de antemano
                neigh_dist = G.edges[node, neighbor]['distance'] + distance
                
                #Comparamos la distancia desde el nodo actual con la que tenía antes el vecino
                if neigh_dist < aux_dist[neighbor]: 
                    aux_dist[neighbor] = neigh_dist
                    heapq.heappush(heap, [neigh_dist ,neighbor])
                    prevs[neighbor] = node
                    #Actualizamos las distancias y quién es el padre más rápido

In [4]:
# Prueba tu algoritmo! 
# El camino esperado es: [10, 128, 39, 145, 89, 277, 192, 107, 133, 146, 236, 99, 74, 17, 110, 265, 1, 73, 182, 194, 5, 252, 251, 235]
dijkstra(G, 10, 235)

{'path': [10,
  128,
  39,
  145,
  89,
  277,
  192,
  107,
  133,
  146,
  236,
  99,
  74,
  17,
  110,
  265,
  1,
  73,
  182,
  194,
  5,
  252,
  251,
  235],
 'expanded': 279,
 'distance': 0.31895111263175857}

In [5]:
algo = dijkstra(G, 10, 235)
path, expanded, distance = algo.get('path'), algo.get('expanded'), algo.get('distance')
print(type(path))
print(type(expanded))
print(type(distance))

<class 'list'>
<class 'int'>
<class 'float'>


<div class="alert alert-success" style="width:90%; margin:0 auto;">

  <h2><p>2- Paradas intermedias</p></h2>
   <p>
 Se propone aquí implementar una variante del algoritmo Dijkstra que encuentre el camino más corto entre dos paradas de metro forzando el mismo a pasar por una serie de paradas intermedias. Por ejemplo, queremos encontrar el camino más corto entre el nodo 10 y 235 pero pasando por el 33 y el 122. El algoritmo debe encontrar el orden idóneo de visita de los nodos intermedios (33 --> 122 o 122 --> 33) sabiendo que empezamos en 10 y acabamos en 235.
</p>

<p></p>

<p>
<b> Nota: </b> Recordad que en Algorítmica Avanzada buscamos la implementación de algoritmos que no solo resuelvan el problema, sino que lo hagan de manera eficiente.
</p>


<div class="alert alert-danger" style="width:80%; margin:0 auto; padding">
<center><p><h3> Código </h3></p> </center>
<p>
<h3>INPUT</h3>
<ul>
<li>__G__: Este es el grafo (en el caso de esta practica la red de metro) que utilizaremos para buscar el camino. Debe de ser un objeto de tipo `nx.Graph`.</li>
<li>__origen__: Este parámetro corresponde al índice de un nodo. En este caso, como indexamos los nodos con el identificador de las paradas de Metro, deberá ser un entero _(e.g. 231)_.</li>
<li>__destino__: El indice del nodo al que queremos llegar. Igual que el origen, deberá ser un entero.</li>
<li>__paradas__: Una lista de índices de nodos por los que queremos pasar de camino entre el origen y el destino. </li>
<li>__infinity=*(int)*__: Parametro opcional en el que definimos que numero nos va bien para utilizar como infinito en el momento de inicializar los pesos de los nodos.</li>
</ul>
<br>
<h3>OUTPUT</h3>
El output de una funcion es un <b>diccionario</b> que contiene los siguientes valores
<ul>
<li>__'ordering'__: Una lista de índices en el orden óptimo de visita. El primer y último elemento de la lista deben corresponderse, respectivamente, con el nodo origen y destino. El resto de elementos de la lista serán todas las paradas solicitadas.</li>
<li>__'expanded'__: El numero de nodos que se han visitado para encontrar la solución.</li>
    <li>__'distance'__: La distancia que se recorrerá desde el origen hasta el destino.</li>
</ul>

</p>


<p>
<b>Nota: </b> No se pide el camino completo entre origen y destino, solo el orden óptimo de visita de los nodos. No obstante, se valorará positivamente la reconstrucción del camino completo. Si lo incluís, añadidlo al diccionario que se devuelve con la clave 'complete_path'.
    </p>
</div>


In [6]:
import itertools
def stops_ordering(G, origen, destino, paradas, infinity=2**32-1):
    aux_total_dist = infinity
    aux_dist = 0
    
    complete_path = []
    aux_path = []
    final_paradas = []
    
    permutations = list(itertools.permutations(paradas))
    expanded = 0
    
    for item in permutations:
        first = dijkstra(G,origen,item[0])
        first_path, first_expanded, first_distance = first.get('path'), first.get('expanded'), first.get('distance')
        expanded += first_expanded
        aux_dist = first_distance
        aux_path = first_path
        
        last = dijkstra(G,item[-1],destino)
        last_path, last_expanded, last_distance = last.get('path'), last.get('expanded'), last.get('distance')
        expanded += last_expanded
        aux_dist += last_distance
        
        for i in range(len(item)-1):
            aux = dijkstra(G,item[i],item[i+1])
            path, aux_expanded, dist = aux.get('path'), aux.get('expanded'), aux.get('distance')
            expanded += aux_expanded
            aux_path.extend(path[1:])
            aux_dist += dist
            
        aux_path.extend(last_path[1:])
        if aux_dist < aux_total_dist:
            aux_total_dist = aux_dist
            final_paradas = item
        
    complete_path = aux_path #complete_path no me acaba de coger bien el camino
    path = [origen]
    path.append(final_paradas)
    path.append(destino)
    return {'ordering': path,'expanded': expanded,'distance': aux_total_dist, 'complete_path': complete_path}

In [7]:
# Prueba tu algoritmo! El orden de recorrido esperado es: [10, 33, 122, 235]
stops_ordering(G, 10, 235, [33,122])

{'ordering': [10, (33, 122), 235],
 'expanded': 1092,
 'distance': 0.5169849201008005,
 'complete_path': [10,
  128,
  39,
  145,
  90,
  104,
  11,
  163,
  82,
  193,
  18,
  186,
  122,
  99,
  236,
  229,
  273,
  248,
  285,
  279,
  13,
  156,
  3,
  295,
  244,
  164,
  33,
  164,
  244,
  295,
  3,
  156,
  13,
  279,
  285,
  248,
  273,
  229,
  236,
  99,
  74,
  17,
  110,
  265,
  1,
  73,
  182,
  194,
  5,
  252,
  251,
  235]}

In [8]:
stops_ordering(G, 10, 33, [87, 35, 122, 92])

{'ordering': [10, (87, 122, 35, 92), 33],
 'expanded': 10512,
 'distance': 0.4179277130219865,
 'complete_path': [10,
  128,
  39,
  145,
  92,
  145,
  90,
  104,
  11,
  163,
  82,
  193,
  18,
  186,
  122,
  99,
  236,
  229,
  273,
  198,
  272,
  245,
  35,
  245,
  191,
  136,
  279,
  87,
  255,
  25,
  161,
  44,
  166,
  263,
  3,
  295,
  244,
  164,
  33]}

<div class="alert alert-warning" style="width:80%; margin:0 auto; padding">
<center><p><h3> Comentarios Dijkstra</h3></p> </center> </div>

### _(En esta sección se os propone explicar como habeis realizado la implementación y cual es la complejidad detallada del algoritmo. Podéis contestar en este mismo bloque)_

He iniciado un heap en el cual guardo el primer nodo junto a su distancia 0 para que se inicialice la distancia del recorrido a 0, no es necesario para la comparación con infinity de otros nodos porque no son añadidos al heap hasta que se descubren como vecinos.
Tras esto voy iterando sobre los vecinos y los voy guardando en el heap ordenándolos por su distancia al nodo desde el que los descubro, además guardo en un diccionario el padre desde el cuál la distancia es menor (en caso de que esto pase también se actualiza la distancia) para luego poder encontrar el camino haciendo uso de un "backtracking".

Pese a que el algoritmo parezca ser de complejidad O(v^2) al tener dos bucles encastados, en realidad se trata de una complejidad de O(e log v) debido a que al usar el heap como para obtener el siguiente nodo reducimos el tiempo computacional necesario para encontrarlo.

<div class="alert alert-warning" style="width:80%; margin:0 auto; padding">
<center><p><h3> Comentarios Orden óptimo de Paradas Intermedias</h3></p> </center> </div>

### _(En esta sección se os propone explicar como habeis realizado la implementación y cual es la complejidad detallada del algoritmo. Podéis contestar en este mismo bloque)_
Debido a que este problema para n número de paradas intermedias se acaba reduciendo a un TSP (Travelling Salesman Problem) y debemos comprobar todas las posibilidades para ver cuál es el camino más corto. Lo que he hecho es generar todas las permutaciones de las paradas con itertools, luego he generado los caminos desde el inicio a la primera parada, después desde la última parada hasta el final y por último el camino entre las paradas para luego comparar cuál tiene la menor distancia entre las diferentes permutaciones.

La complejidad de esto será de O(k! * e log v). Siendo k el número de paradas intermedias, e las aristas y v los vértices.

<div class="alert alert-info">
<center>
  <h1>Entrega</h1>
</center>
<p>
La entrega de esta práctica se podrá realizar en el campus virtual hasta el día <b>27 de Octubre a las 23:55</b>. En la tarea que se habilitará en el campus deberéis colgar únicamente este notebook con el nombre:
</p>
<p>
```
* [grupo]_[apellido]_[nombre]_1-Grafos.ipynb
```

</p>
<p>
    Por ejemplo, para un alumno llamado <i>Nombre Genérico</i> perteneciente al <i>grupo Z</i> el nombre del archivo debería ser:
</p>
<p>
```
Z_Generico_Nombre_1-Grafos.ipynb
```

</p>
<p>

Es muy importante que en el notebook exista <b> una sola función </b> con el nombre <i>dijkstra</i> y <i>stops_ordering</i> ya que emplearemos un corrector automático para agilizar el proceso. No os preocupéis si no os funciona del todo, el no pasar los tests no significa necesariamente que tengáis un 0 en la práctica; también revisaremos manualmente el código así como los comentarios del final del notebook y vuestro análisis de complejidad.


Es fundamental que el código esté bién comentado y con un análisis de complejidad exhaustivo del algoritmo. La importancia de poner nombre correcto al archivo debería ser directamente proporcional a lo contentos que queráis que los profesores de prácticas corrijan.
</p>
</div>